In [41]:
from semanticscholar import SemanticScholar

In [42]:
# sch = SemanticScholar()
# paper = sch.get_paper('10.1093/mind/lix.236.433')
# print(paper.title)


In [43]:
# sch = SemanticScholar()
# response = sch.search_paper(query='deep learning', bulk=True)


In [44]:
import json
# from semanticscholar import SemanticScholar

sch = SemanticScholar()
response = sch.search_paper(query="machine learning", bulk=True)
response=response.raw_data
# Pretty-print the JSON response
print(json.dumps(response, indent=4))
top_10_results = response[:2]

# # Pretty-print the top 10 results
# print(json.dumps(top_10_results, indent=4))


[
    {
        "paperId": "00000c33779acab142af6c7a6dae8b36fac0805d",
        "externalIds": {
            "DOI": "10.3390/en17040925",
            "CorpusId": 267729693
        },
        "corpusId": 267729693,
        "publicationVenue": {
            "id": "1cd505d9-195d-4f99-b91c-169e872644d4",
            "name": "Energies",
            "type": "journal",
            "issn": "1996-1073",
            "url": "http://www.e-helvetica.nb.admin.ch/directAccess?callnumber=bel-155563",
            "alternate_urls": [
                "http://nbn-resolving.de/urn/resolver.pl?urn=urn:nbn:ch:bel-155563",
                "https://www.mdpi.com/journal/energies",
                "http://www.mdpi.com/journal/energies"
            ]
        },
        "url": "https://www.semanticscholar.org/paper/00000c33779acab142af6c7a6dae8b36fac0805d",
        "title": "Insights into Household Electric Vehicle Charging Behavior: Analysis and Predictive Modeling",
        "abstract": "In the era of burgeoning e

In [45]:
print(len(response))

1000


In [46]:
import csv
csv_filename = "papers.csv"

# Open CSV file for writing
with open(csv_filename, mode="w", newline="", encoding="utf-8") as file:
    writer = csv.writer(file)

    # Write header row
    writer.writerow(["Paper ID", "DOI", "Title", "Abstract", "Venue", "publicationType", "publication_type_2", "journal_name", "pages", "volume", "Year", "publicationDate", "Citations", "References", "Authors", "Author Ids", "URL", "s2FieldsOfStudys"])

    # Write data rows
    for paper in response:
        paper_id = paper["paperId"]    
        doi = paper["externalIds"].get("DOI", "Unknown")  # Get DOI if available
        title = paper["title"]
        abstract= paper["abstract"]
        venue = paper["venue"]
        # publication_type = paper.get("publicationVenue", {}).get("type", "Unknown")
        publication_type = (paper.get("publicationVenue") or {}).get("type", "Unknown")
        # publication_type = (paper.get("publicationVenue") or {}).get("type", "Unknown")
        publication_type_2 = paper.get("publicationTypes", [])
        journal_name=(paper.get("journal") or {}).get("name", "Unknown") 
        pages = (paper.get("journal") or {}).get("pages", "Unknown") 
        volume = (paper.get("journal") or {}).get("volume", "Unknown") 

        year = paper["year"]
        publicationDate= paper["publicationDate"]
        citation_count = paper["citationCount"]
        reference_count = paper["referenceCount"]
        s2FieldsOfStudys = ', '.join(sorted({s2FieldsOfStudy['category'] for s2FieldsOfStudy in paper["s2FieldsOfStudy"]}))
        
        # Format authors as "Name (Author ID)"
        authors = ", ".join(f"{author['name']}" for author in paper["authors"])
        authorsIds = ", ".join(f"{author['authorId']}" for author in paper["authors"])

        url = paper["url"]

        writer.writerow([paper_id, doi, title, abstract, venue, publication_type, publication_type_2, journal_name, pages, volume, year, publicationDate, citation_count, reference_count, authors, authorsIds, url, s2FieldsOfStudys])

print(f"CSV file '{csv_filename}' has been created successfully.")

CSV file 'papers.csv' has been created successfully.


In [47]:
# # paper_ids_arr =[paper["externalIds"].get("DOI") for paper in top_10_results]
# # print(paper_ids_arr)

# paper_ids_arr = [paper["externalIds"].get("DOI") for paper in top_10_results if paper["externalIds"].get("DOI") is not None]
# print(paper_ids_arr)

In [48]:
paper=sch.get_paper('10.1109/ICCNS58795.2023.10193141')
# paper=sch.get_paper('00000c33779acab142af6c7a6dae8b36fac0805d')
print(json.dumps(paper.raw_data, indent=4))

{
    "paperId": "00005d68c6c7eb4d3c27da8242a30b9a498f991e",
    "externalIds": {
        "DOI": "10.1109/ICCNS58795.2023.10193141",
        "CorpusId": 260386021
    },
    "corpusId": 260386021,
    "publicationVenue": {
        "id": "3c4447e5-bf74-426d-ac93-650df74ea250",
        "name": "International Conference on Communication and Network Security",
        "type": "conference",
        "alternate_names": [
            "ICCNS",
            "Int Conf Commun Netw Secur"
        ]
    },
    "url": "https://www.semanticscholar.org/paper/00005d68c6c7eb4d3c27da8242a30b9a498f991e",
    "title": "Detection of DDoS Attacks on Clouds Computing Environments Using Machine Learning Techniques",
    "abstract": "The growing number of cloud-based services has led to a rising threat of Distributed Denial of Service (DDoS) attacks. These attacks can cause significant harm to businesses and organizations by overwhelming their network resources, resulting in the unavailability of critical service

In [49]:
import csv

# Filter out None values from paper_ids_arr
paper_ids_arr = [paper["externalIds"].get("DOI") for paper in top_10_results if paper["externalIds"].get("DOI")]

# Open CSV file to store results
with open("reference_papers.csv", "w", newline="") as csvfile:
    writer = csv.writer(csvfile)

    # Write the header
    writer.writerow(["Paper DOI", "Reference DOI", "Reference Paper ID", "Title", "Abstract", "Venue", "Year","Authors"])

    # Iterate over each DOI, fetch the paper, and extract reference DOIs and paper IDs
    for doi in paper_ids_arr:
        paper = sch.get_paper(doi)  # Fetch paper details
        
        if paper and hasattr(paper, "references"):  # Ensure valid response
            for reference in paper.references:
                ref_paper_id = getattr(reference, "paperId", "N/A")
                
                # Ensure externalIds is not None before accessing "DOI"
                ref_doi = reference.externalIds["DOI"] if reference.externalIds and "DOI" in reference.externalIds else "N/A"
                ref_title= getattr(reference, "title", "N/A")
                ref_abstract= getattr(reference, "abstract", "N/A")
                ref_venue= getattr(reference, "venue", "N/A")
                ref_year= getattr(reference, "year", "N/A")
                ref_author=reference.authors["name"] if reference.authors and "name" in reference.authors else "N/A"


                # Write reference DOI and Paper ID to CSV
                writer.writerow([doi, ref_doi, ref_paper_id, ref_title, ref_abstract, ref_venue, ref_year, ref_author])

print("Data has been written to 'reference_papers.csv'")


Data has been written to 'reference_papers.csv'


In [50]:
# paper_ids_arr = [paper["doi"] for paper in top_10_results]
# print(paper_ids_arr)


# all_references = {}

# # Iterate over the paper_ids_arr
# for paper_id in paper_ids_arr:
#     # Get the paper by its paper_id
#     paper = sch.get_paper(paper_id)
#     references = paper.references

#     # Create a list to store the reference paperIds for this paper
#     paper_ids = []

#     # Iterate over the references and extract paperId
#     for reference in references:
#         paper_ids.append(reference['paperId'])

#     # Store the reference paperIds in the dictionary with paper_id as the key
#     all_references[paper_id] = paper_ids

# # Print the reference paperIds for all papers
# for paper_id, references in all_references.items():
#     print(f"Paper ID: {paper_id} - Reference Paper IDs: {references}")

In [51]:
# paper_ids_arr = [paper["DOI"] for paper in top_10_results]
# # print(paper_ids_arr)

# # Open a CSV file for writing
# with open('paper_references.csv', mode='w', newline='') as file:
#     writer = csv.writer(file)
    
#     # Write the header row
#     writer.writerow(["Paper_ID", "Reference_Paper_IDs"])
    
#     # Iterate over the paper_ids_arr
#     for paper_id in paper_ids_arr:
#         # Get the paper by its paper_id
#         paper = sch.get_paper(paper_id)
#         references = paper.references

#         # Create a list to store the reference paperIds for this paper
#         reference_paper_ids = []

#         # Iterate over the references and check if paperId exists
#         for reference in references:
#             # Access paperId as an attribute directly
#             ref_paper_id = getattr(reference, 'paperId', None)
#             if ref_paper_id is not None:
#                 reference_paper_ids.append(ref_paper_id)
#             else:
#                 reference_paper_ids.append("No Paper ID")  # or skip it as needed

#         # Write the paper_id and the corresponding reference paper IDs to the CSV file
#         writer.writerow([paper_id, ', '.join(reference_paper_ids)])

# print("Data has been written to 'paper_references.csv'")

In [52]:
# # paper = sch.get_paper('10.1093/mind/lix.236.433')
# paper=sch.get_paper('10.3390/en17040925')
# # paper=sch.get_paper('00000c33779acab142af6c7a6dae8b36fac0805d')
# print(json.dumps(paper.raw_data, indent=4))

In [53]:
# # paper = sch.get_paper('10.1093/mind/lix.236.433')
# # print(json.dumps(paper.raw_data, indent=4))
# # import json
# # from semanticscholar import SemanticScholar

# # # Initialize the Semantic Scholar API client
# # sch = SemanticScholar()

# # Paper ID
# paper_id = '10.1093/mind/lix.236.433'
# # paper_id='2d5673caa9e6af3a7b82a43f19ee920992db07ad'

# # Fetch paper details
# paper = sch.get_paper(paper_id)

# # Extract citations (direct access to attribute)
# # citations = paper.citations  # Accessing the citations attribute
# references=paper.references
# # print(references)

# paper_ids = []

# # Iterate over the references and extract paperId
# for reference in references:
#     paper_ids.append(reference['paperId'])

# # Print the paperIds
# print(paper_ids)

# # Convert each citation to a dictionary
# # citations_dict = []
# # for citation in references:
# #     citation_data = {
# #         "paperId": citation.paperId,
#         # "title": citation.title,
#         # "year": citation.year,
#         # "authors": [author.name for author in citation.authors],
#         # "url": citation.url
#     # }
#     # citations_dict.append(citation_data)

# # Pretty-print the citations as JSON
# # print(json.dumps(citations_dict, indent=4))





In [54]:
# import json
# from semanticscholar import SemanticScholar

# sch = SemanticScholar()
# response = sch.search_paper(query="deep learning", bulk=True)

# # Ensure response is a list
# papers = response.raw_data if isinstance(response.raw_data, list) else []

# # Get up to 1000 results safely (if available)
# top_results = papers[:1000]

# # Filter papers where publication type includes "Conference"
# conference_papers = [
#     paper for paper in top_results 
#     if isinstance(paper.get("publicationTypes"), list) and "Conference" in paper["publicationTypes"]
# ]

# # Pretty-print filtered results
# print(json.dumps(conference_papers, indent=4))


In [55]:
# import json
# from semanticscholar import SemanticScholar

# sch = SemanticScholar()
# response = sch.search_paper(query="deep learning", bulk=True)

# # Get only the top 10 results
# top_10_results = response.raw_data[:1000]

# # Extract and print publication types
# for i, paper in enumerate(top_10_results, 1):
#     pub_type = paper.get("publicationTypes", "Unknown")  # Default to 'Unknown' if missing
    
#     # Ensure pub_type is always a list before joining
#     if isinstance(pub_type, list):
#         pub_type_str = ", ".join(pub_type)
#     else:
#         pub_type_str = str(pub_type)

#     print(f"Paper {i} - Publication Type: {pub_type_str}")


In [56]:
# # from semanticscholar import SemanticScholar
# # sch = SemanticScholar()
# # paper = sch.get_paper('10.1093/mind/lix.236.433')
# author = sch.get_author(2262347)
# print(json.dumps(author.raw_data, indent=4))


In [57]:
api_key = "2qjngc1ewhfQAW7Bkts9FOIYvZR8V03T"
# with open ("apikey.txt", "r") as apikey_file:
#     api_key=apikey_file.readlines()[0].strip()
api_endpoint = "https://api.core.ac.uk/v3/"

In [58]:
# import pandas
# from matplotlib import rcParams 
# import requests 
# import json 
# import seaborn as sns 
# import itertools 
# from datetime import datetime 
# import matplotlib.pyplot as plt 
# import networkx as nx 
# import hashlib 
# import os 
# from operator import itemgetter

# rcParams['figure.figsize'] = 11.7,8.27

# def pretty_json(json_object): print(json.dumps(json_object, indent=2))

In [59]:
# def get_entity(url_fragment):
#     headers={"Authorization":"Bearer "+api_key}
#     response = requests.get(api_endpoint + url_fragment, headers=headers)
#     if response.status_code == 200:
#         return response.json(), response.elapsed.total_seconds()
#     else:
#         print(f"Error code {response.status_code}, {response.content}")

In [60]:
# data_provider, elapsed = get_entity("data-providers/1")
# pretty_json(data_provider)

In [61]:
# def query_api(url_fragment, query,limit=100):
#     headers={"Authorization":"Bearer "+api_key}
#     query = {"q":query, "limit":limit}
#     response = requests.post(f"{api_endpoint}{url_fragment}",data = json.dumps(query), headers=headers)
#     if response.status_code ==200:
#         return response.json(), response.elapsed.total_seconds()
#     else:
#         print(f"Error code {response.status_code}, {response.content}")

In [62]:
# results , elapsed = query_api("search/data-providers", "location.countryCode:gb")

# pretty_json(results)